# Data PreProcessing

In [1]:
import pandas as pd
Friends_Resumes_data=pd.read_csv('Friends_resumes.csv')
Friends_Resumes_data=list(Friends_Resumes_data['data'])
scrapper_resumes=pd.read_csv('Resume_dataset.csv')
scrapper_resumes=list(scrapper_resumes['data'])
Resume_data_set=Friends_Resumes_data+scrapper_resumes

for Resume in range(len(Resume_data_set)):
    if Resume_data_set[Resume] is None:
        Resume_data_set.pop(Resume)

In [45]:
# Apply Regular Expressions to remove unwanted data
import re

patterns = ['\d{11}','\d{4}-\d{7}', '[a-z0-9]*@gmail.com','linkedin.com[\/ a-z-0-9A-Z]*','Resume','resume','Resume Headline','github.com[\/ a-z-0-9:.A-Z]*','Pakistan','Lahore','india','India','INDIA']
combined_pattern = '|'.join(patterns)
pattern=re.compile(combined_pattern)

for Resume in range(len(Resume_data_set)):
    Resume_data_set[Resume] = pattern.sub('',Resume_data_set[Resume])

In [52]:
# Remove Extra \n and tabs
for Resume in range(len(Resume_data_set)):
    Resume_data_set[Resume]=Resume_data_set[Resume].replace('\t','')
    Resume_data_set[Resume]=Resume_data_set[Resume].replace('\n','')

In [39]:
# Remove multiple spaces
for resume in range(len(Resume_data_set)):  
    text = Resume_data_set[resume]
    new_text = re.sub(r"\s+", " ", text)
    Resume_data_set[resume]= new_text

for resume in range(len(Resume_data_set)):
    Resume_data_set[resume].replace("|","")

In [50]:
# to preprocess data
import spacy
Model=spacy.load('en_core_web_sm')
for resume in range(len(Resume_data_set)):
    doc=Model(Resume_data_set[resume])
    
    tokens_list=[]
    para=''
    for token in doc:
        if(not(token.is_punct)):
            tokens_list.append(token.lemma_)
        para=' '.join(tokens_list)
    Resume_data_set[resume]=para

In [59]:
final_datset=pd.DataFrame({'data':Resume_data_set})
final_datset.to_csv('Final_resumes_data_set.csv')

In [62]:
#import pandas as pd
Requirements_data=pd.read_csv('Requirements_data.csv')
Requirements_data=list(Requirements_data['Data'])

In [68]:
for requirement in range(len(Requirements_data)):
    Requirements_data[requirement]=Requirements_data[requirement].replace('\t','')
    Requirements_data[requirement]=Requirements_data[requirement].replace('\n','')

In [70]:
for requirement in range(len(Requirements_data)):
    doc=Model(Requirements_data[requirement])
    
    tokens_list=[]
    para=''
    for token in doc:
        if(not(token.is_punct)):
            tokens_list.append(token.lemma_)
        para=' '.join(tokens_list)
    Requirements_data[requirement]=para

In [30]:
Data_set=Resume_data_set+Requirements_data
whole_datset=pd.DataFrame({'data':Data_set})
whole_datset.to_csv('Whole_data_set.csv')

In [1]:
import pandas as pd
Data_set=pd.read_csv('Whole_data_set.csv')
Data_set=list(Data_set['data'])

In [3]:
import tensorflow as tf
from tensorflow.keras import models,layers

In [4]:
#seperate feature and target data
data=[]
vocab=set()
word_to_index={}
init_index=0
window_size=2

for statemnt in Data_set:
    tokens=statemnt.split()
    for token in tokens:
        if token not in vocab:
            vocab.add(token)
            word_to_index[token]=init_index
            init_index+=1

for statement in Data_set:
    tokens=statement.split()
    for i in range(window_size,len(tokens)-window_size):
        context=[word_to_index[tokens[i+j]] for j in range(-window_size,window_size+1) if j!=0]
        target=word_to_index[tokens[i]]
        data.append((context,target))

In [15]:
with open("word_to_index.pkl", "wb") as f:
    pickle.dump(word_to_index, f)

In [5]:
print('Vocabulary size ', len(vocab))
print('Size of CBOW dataset', len(data))

Vocabulary size  15532
Size of CBOW dataset 823628


In [6]:
import numpy as np
context_data=np.array([context for context, _ in data])
target=np.array([target for _,target in data])
print(len(context_data))
print(len(target))

823628
823628


# Model Training

In [7]:
vocab_size=len(vocab)
model=models.Sequential([
    layers.Embedding(vocab_size,100,input_length=2*window_size),
    layers.GlobalAveragePooling1D(),
    
    layers.Dense(512,activation='relu'),
    layers.Dropout(0.5),
    layers.Dense(256,activation='relu'),
    layers.Dropout(0.5),
    layers.Dense(128,activation='relu'),
    layers.Dropout(0.5),
    layers.Dense(64,activation='relu'),
    layers.Dropout(0.5),
    
    layers.Dense(vocab_size,activation='softmax')
])
model.compile(optimizer='Adam',loss='sparse_categorical_crossentropy',metrics=['accuracy'])

In [8]:
model.fit(context_data,target,epochs=15)

Epoch 1/15


25739/25739 [==============================] - 962s 37ms/step - loss: 5.9944 - accuracy: 0.1007
Epoch 2/15
25739/25739 [==============================] - 955s 37ms/step - loss: 5.3760 - accuracy: 0.1606
Epoch 3/15
25739/25739 [==============================] - 949s 37ms/step - loss: 5.2821 - accuracy: 0.1767
Epoch 4/15
25739/25739 [==============================] - 949s 37ms/step - loss: 5.2682 - accuracy: 0.1827
Epoch 5/15
25739/25739 [==============================] - 951s 37ms/step - loss: 5.2742 - accuracy: 0.1851
Epoch 6/15
25739/25739 [==============================] - 949s 37ms/step - loss: 5.2923 - accuracy: 0.1860
Epoch 7/15
25739/25739 [==============================] - 952s 37ms/step - loss: 5.3143 - accuracy: 0.1860
Epoch 8/15
25739/25739 [==============================] - 939s 36ms/step - loss: 5.3371 - accuracy: 0.1855
Epoch 9/15
25739/25739 [==============================] - 920s 36ms/step - loss: 5.3552 - accuracy: 0.1849
Epoch 10/15
25739/25739 [==========

In [9]:
import pickle

with open("Resume_model.pkl", "wb") as f:
    pickle.dump(model, f)

# with open("Resume_model.pkl", "rb") as f:
#     model = pickle.load(f)


In [10]:
word_embeddings=model.layers[0].get_weights()[0]

In [11]:
for word,idx in word_to_index.items():
    print(f'{word} : {word_embeddings[idx]}')

Abdullah : [ 4.09102552e-02 -7.75327533e-03  1.74126074e-01 -6.83341175e-02
  6.29149526e-02 -1.31882593e-01 -1.28342509e-01  8.87928382e-02
 -1.04108162e-01  1.33561641e-01  1.16381221e-01  1.75160110e-01
  2.24951178e-01 -2.99368035e-02  1.14257485e-01 -3.06200594e-01
  5.38642444e-02 -3.77320349e-02  5.65077029e-02  2.26656608e-02
 -3.15557241e-01 -8.25470015e-02 -5.98762073e-02 -6.95204437e-02
  1.61200151e-01  8.71279985e-02 -2.53852215e-02 -1.31138608e-01
  3.36135253e-02 -1.16366081e-01 -6.83725998e-02 -1.94538638e-01
 -2.30719566e-01  9.38397739e-03 -4.88408245e-02  1.48588002e-01
 -3.49042803e-01  9.51403379e-02 -1.56032056e-01 -1.85111910e-01
 -1.58047825e-02  4.40420397e-02 -2.68395066e-01 -1.93189383e-01
  1.56469554e-01  3.59150134e-02 -2.52345949e-02  2.07602745e-03
  1.45993561e-01 -3.31511170e-01 -1.91500872e-01  1.16894431e-01
  1.07862353e-01 -1.93487436e-01 -5.14556244e-02  1.71447113e-01
 -5.41821076e-03 -2.39509702e-01 -5.41114062e-02 -1.70071989e-01
  1.56201661e-

JWT : [ 0.11370276  0.5617152  -0.18261938 -0.3723579  -0.64087397  0.38927457
  0.10790867 -0.00279    -0.18365526 -0.25516197  1.1981674  -0.28719312
 -0.00813012  0.7575445  -0.8320131   0.58985686 -0.07039525  0.81735986
 -0.02226883  0.33408135  0.56009233  0.30922848 -0.1354722  -0.33654642
 -0.21545656  0.19281147  0.33447796  0.02003179  0.995985   -0.14616404
 -0.52246946  0.23267345  0.01063575  0.29610878  0.72635263  0.2799995
  0.20406547 -0.2938297   0.42401606  0.29097176 -0.3544017  -0.6484383
 -0.0583369   0.03424255 -0.4080053   0.4831252   0.23138468 -0.7698118
  0.26142466 -0.07001604 -0.38285664 -0.38693562 -0.15269193  0.89235014
  0.4645696  -0.3818546   0.35984176 -0.16163085 -0.7099025   0.26046312
  0.13909516  0.02071866  0.15834302  0.21657003  0.10342748  0.54767513
  0.27710363  0.21663553 -0.78979367 -0.7256821   0.2967489   0.17735747
 -0.36423197 -0.5991569  -0.16826802 -0.06842953 -0.4239911   0.33564383
 -0.14431894 -0.39919272  0.53803706  0.14553335

Country : [ 0.0461499   0.14647457  0.19805738  0.24790856  0.37799346 -0.35794368
 -0.08709196  0.10818738 -0.5231354   0.5563423  -0.6895543  -0.09742738
 -0.28062654  0.3916374   1.0296346  -0.468514    0.3340511  -0.14217466
  0.05782669  0.2679721   0.11875548 -0.10376301  0.26790726 -0.25179723
  0.43877134 -0.39984143 -0.61340266 -0.19107997 -0.07684091 -0.17111313
 -0.1764263  -0.18315989  0.24054956  0.13044806  0.23909782 -0.15179771
 -0.34913373  0.04357588 -0.23493545 -0.24799809 -0.20762746 -0.16959698
 -0.19373584 -0.21743327  0.46431103  0.18232742  0.13658306  0.31572366
 -0.42880213  0.2974454   0.21118514  0.19335085 -0.34749785  0.19133386
 -0.16530134  0.44894695  0.17236847 -0.09265178  0.11580081 -0.2653252
  0.18767215 -0.4747172  -0.08467586 -0.02489528 -0.46266183  0.04808812
 -0.28987503 -0.35321176 -0.17400086  0.2545326  -0.5776034  -0.68956524
 -0.12384575 -0.29144782 -0.2630276   0.9991325   0.92251027  0.10767867
  0.4786029  -0.06290329 -0.39022604 -0.20

Binance : [ 0.04650982 -0.2058185  -0.01639437 -0.13558467  0.00950552 -0.2350086
  0.07451104 -0.00567873 -0.0842866   0.29293352 -0.06302227 -0.02922639
 -0.01849562  0.13808748  0.00193475 -0.11077769 -0.26277286 -0.03964852
 -0.15313996  0.20794752 -0.13361767 -0.11216505  0.09855833 -0.03641988
 -0.14814404  0.0411648  -0.00810594  0.05695049  0.06169794  0.22152524
 -0.14364137 -0.06519229 -0.10168397  0.01014092 -0.23380342  0.1728911
 -0.01272598  0.04944074 -0.12806581 -0.22435379 -0.01137114 -0.01393619
 -0.13579556  0.12947948  0.09566684  0.13479303  0.03518843 -0.22535263
  0.08368152 -0.25192186 -0.06391474 -0.1729341   0.19215222  0.08265539
 -0.01811387  0.1387579   0.03840861  0.05755336  0.30161902 -0.25266722
  0.10120615  0.08178035  0.08922556  0.08328898 -0.03758623 -0.13704559
  0.15165226 -0.09014174  0.14829531 -0.01671661 -0.1253092   0.05255077
  0.18816149  0.1454468   0.04671211  0.09931982  0.07732905 -0.23919854
 -0.0068242   0.07927185 -0.05535448 -0.025

foundation : [-4.05258685e-01  1.15081221e-01 -1.33041561e-01 -3.45712036e-01
 -4.98128474e-01  1.60139963e-01 -1.37782562e+00  1.11771631e+00
  6.83642268e-01  1.95004687e-01  1.15209378e-01 -2.47952566e-01
  7.32415974e-01  5.94819300e-02  3.99707675e-01  1.47919104e-01
 -1.24203682e-01 -3.97348285e-01 -2.00973615e-01 -4.22429949e-01
 -4.98151332e-01  3.19608182e-01  1.91684872e-01  7.16859996e-01
  2.29623839e-01  8.52572620e-01  4.93523300e-01 -1.63167015e-01
  6.27916336e-01  9.18406248e-01 -6.28029183e-02  1.19753882e-01
 -1.36154771e-01 -1.02544583e-01 -1.63803950e-01 -4.19405997e-01
  3.95599306e-01  3.77030253e-01  8.45883846e-01 -5.54455519e-01
  1.00171065e+00 -5.71049511e-01  1.10787356e+00  8.05377901e-01
  4.87232655e-01 -8.91029775e-01 -8.92103076e-01  9.22784209e-04
 -4.92145382e-02  2.55436271e-01  8.66784811e-01  2.82163061e-02
  4.87885177e-01  9.97749746e-01  4.83665675e-01 -3.54214340e-01
  8.51735711e-01 -3.51707965e-01 -1.46856263e-01  7.42811263e-01
 -2.54620790

...

Manfuacturing : [ 0.00790159  0.34449565  0.21012399  0.1576779   0.10142795  0.26387212
 -0.14076322 -0.01262577  0.23071995 -0.1211279   0.09987041 -0.36226073
 -0.12163624 -0.00221427  0.1765152  -0.30332494 -0.19696704  0.08601097
 -0.10451961 -0.06500259 -0.162415    0.09847865  0.01977371 -0.4074659
  0.38987365 -0.03722853 -0.07901379  0.1182391  -0.04439041  0.07848423
 -0.03447653  0.04436083  0.13484217 -0.3029805   0.14888112  0.02004983
  0.03759426  0.05007005  0.23468599  0.02160583  0.23956817 -0.16748731
  0.542846   -0.10338681  0.04867391 -0.10670204 -0.3580694  -0.05092968
 -0.22343788  0.05845191  0.11329155  0.22014824 -0.02488576 -0.20289089
  0.42278987  0.02498556 -0.13137396 -0.0563461   0.08359948  0.36837584
  0.24380744  0.02233094 -0.1500041  -0.04365663 -0.42492965  0.08022923
  0.1774166   0.12808244  0.27396318 -0.12363569  0.09533267 -0.00118351
  0.01912416 -0.52057064 -0.58439046  0.27289847  0.3528744   0.03484713
  0.06194129 -0.01925389  0.0721092 

composition : [-0.23831922  0.16576669 -0.23843966  0.34352425  0.07203096  0.24860142
 -0.2615581  -0.21034202  0.2872231   0.0438339  -0.17289296  0.05767891
  0.28270185 -0.14868414 -0.0469653   0.25921273  0.34431958  0.16684876
 -0.0797767  -0.00937749 -0.22644287  0.0660721  -0.01116505 -0.15299557
 -0.11260199 -0.0207739  -0.24464616 -0.49386412 -0.12573905 -0.12721017
  0.3310766  -0.2847186   0.10880007  0.10291931  0.3389955  -0.27204162
 -0.24296042  0.04119198  0.4857271   0.02421213 -0.07839715  0.14276661
 -0.19622259 -0.16888657 -0.08163821  0.00675814 -0.14632966 -0.12991849
 -0.1711065   0.2054703  -0.15827967  0.25164568 -0.11306691 -0.33269528
  0.11404141 -0.08994553  0.2920554   0.06252015  0.64669746  0.31031817
 -0.09073497  0.21553211 -0.12347437  0.22857659 -0.2736938  -0.0336487
 -0.08035672  0.34659925  0.01109485  0.18422635  0.15990075  0.06277417
 -0.12939434  0.20516382 -0.29002833  0.2996802   0.31869987  0.4005977
 -0.07706132  0.14616421  0.5512006  -0

DSDS : [ 3.1838827e-02 -1.0195549e-01 -4.9768392e-02  3.7349764e-01
  3.1978711e-01  8.6606145e-02  7.9265311e-02  1.8599997e-01
 -1.7024000e-01  1.9604644e-01  2.5951326e-01 -1.5631761e-02
  1.3514881e-01  3.1213388e-01 -2.6891092e-02  1.0019468e-01
 -1.2546468e-01 -8.7250456e-02  7.7608772e-02 -4.2245656e-02
 -1.0673014e-01  1.0517241e-02  1.4066850e-01  2.5715494e-01
  1.7142369e-01  1.2416424e-01  2.5423765e-01  3.3493832e-02
 -9.1613159e-02 -1.1169224e-04 -4.6026221e-01  2.7246645e-01
  6.0361153e-01  4.3083721e-01  4.0742210e-01  4.8422506e-01
 -1.1578043e-01  1.8044645e-01 -5.4448746e-02  6.6960432e-02
 -1.7286530e-01 -1.6242197e-01 -2.7966911e-01 -1.8662335e-01
  2.0197015e-01  5.3904139e-02 -1.0534447e-01 -3.3462275e-02
  1.1017767e-01 -1.2284243e-01 -1.4066467e-01  1.7314680e-01
  1.0203108e-01 -2.9443748e-02 -4.9635464e-01  3.4512594e-01
  1.1634448e-01  2.2123791e-01  1.9228679e-01  4.2709935e-01
 -1.9672456e-01  2.3198874e-01  3.1275174e-01 -7.6594204e-02
 -1.1356708e-01 -

learningSolid : [ 4.8316115e-01  9.0045229e-02 -1.3915981e-01  1.9809598e-02
  1.5275598e-01 -8.9833719e-01  1.7841940e-01 -2.0469496e-01
  5.9227681e-01  3.6968774e-01  3.9442942e-02 -3.1951854e-01
 -4.1121700e-01  1.1746116e+00  3.6339810e-01 -5.0084382e-01
 -5.0963628e-01 -6.2227643e-01 -5.5507079e-02  7.1062416e-01
  2.6920506e-01 -9.9166349e-02 -7.3679215e-01  6.8919927e-01
  5.9123856e-01 -3.3446148e-01  1.0076739e-01  4.0986890e-01
  8.7063447e-02  4.2799512e-01 -8.1837820e-03  4.4660246e-01
  2.7651930e-01 -4.2978841e-01 -4.3957508e-01  4.4599053e-01
  4.0851375e-01  1.9501321e-01 -4.1734630e-01 -3.4590858e-01
 -1.6918249e-01 -4.8260543e-01  5.9351504e-01  4.0124995e-01
 -2.3323368e-02 -7.1200317e-01 -4.6882275e-01  5.9715816e-04
  1.1261419e-01  2.3409426e-01  2.1520175e-01 -5.2927506e-01
 -5.7681628e-02  4.8030031e-01 -1.1073359e-01 -6.1578476e-01
  5.7256848e-01  5.3060943e-01 -2.6707113e-01  7.7219123e-01
 -1.8652824e-01 -7.1842486e-01  7.5113475e-02  1.5952829e-01
  3.0097

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

